In [0]:
import random
import numpy as np
import pickle

In [29]:
%tensorflow_version 2.x
import tensorflow
print(tensorflow.__version__)

2.0.0


In [0]:

import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from sklearn.decomposition import PCA

import pickle
import numpy as np
import matplotlib.pyplot as plt
from tensorflow.keras.utils import plot_model

%matplotlib inline
%config InlineBackend.figure_format = 'retina'

In [31]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [0]:
from tensorflow import keras
from tensorflow.keras.models import Sequential
from tensorflow.keras.models import Sequential
from tensorflow.keras.preprocessing.image import ImageDataGenerator
from tensorflow.keras.layers import Dense, Activation, Flatten, Dropout, BatchNormalization
from tensorflow.keras.layers import Conv2D, MaxPooling2D
from tensorflow.keras import regularizers, optimizers

%matplotlib inline
import matplotlib.pyplot as plt
import numpy as np
import time


In [0]:
ROOT = '/content/drive/My Drive/19 Fall/CSE 569/Project'

# Loss function
https://stackoverflow.com/a/52131163

In [0]:
def custom_loss(Y, A):
  P = tensorflow.keras.backend.max(Y, axis=1)
  # P = tensorflow.keras.backend.print_tensor(P, message="P is: ")

  # Labeled encodings will have max = 1
  Y_l = tensorflow.boolean_mask(Y, tensorflow.equal(P, 1))
  A_l = tensorflow.boolean_mask(A, tensorflow.equal(P, 1))
  # Y_l = tensorflow.keras.backend.print_tensor(Y_l, message="Y_l is: ")
  # A_l = tensorflow.keras.backend.print_tensor(A_l, message="A_l is: ")
  A_l_log = tensorflow.keras.backend.log(A_l)
  A_l = tensorflow.keras.backend.flatten(A_l)
  A_l_log = tensorflow.keras.backend.flatten(A_l_log)
  A_l_log = tensorflow.keras.backend.abs(A_l_log)
  Y_l = tensorflow.keras.backend.flatten(Y_l)

  # Y_l = tensorflow.keras.backend.print_tensor(Y_l, message="Y_l flattened is: ")
  # A_l_log = tensorflow.keras.backend.print_tensor(A_l_log, message="A_l_log flattened is: ")

  L_l = A_l_log * Y_l
  L_l = tensorflow.boolean_mask(L_l, tensorflow.greater(L_l, 0))
  L_l = tensorflow.keras.backend.mean(L_l)
  # L_l = tensorflow.keras.backend.print_tensor(L_l, message="L_l is: ")

  # Unlabeled encodings will have max less than 1
  Y_u = tensorflow.boolean_mask(Y, tensorflow.less(P, 1))
  A_u = tensorflow.boolean_mask(A, tensorflow.less(P, 1))
  # Y_u = tensorflow.keras.backend.print_tensor(Y_u, message="Y_u is: ")
  # A_u = tensorflow.keras.backend.print_tensor(A_u, message="A_u is: ")
  A_u_log = tensorflow.keras.backend.log(A_u)
  # A_u_log = tensorflow.keras.backend.print_tensor(A_u_log, message="A_u_log is: ")
  A_u = tensorflow.keras.backend.flatten(A_u)
  A_u_log = tensorflow.keras.backend.flatten(A_u_log)
  A_u_log = tensorflow.keras.backend.abs(A_u_log)
  L_u = A_u * A_u_log
  L_u = tensorflow.keras.backend.mean(L_u)
  # L_u = tensorflow.keras.backend.print_tensor(L_u, message="L_u is: ")

  # L = 0 - L_l - L_u
  L = L_l + L_u
  # L = tensorflow.keras.backend.print_tensor(L, message="L is: ")
  # first param is loss during training which includes unlabeled samples and won't throw nan
  # second param is loss during validation which only has labeled samples so returning only labeled error to avoid nan
  return tensorflow.keras.backend.in_train_phase(L/1, L_l/1)


# Model

In [35]:
# Define the model
num_filters = 32

model = Sequential()
model.add(Conv2D(num_filters, (3,3), padding='same', input_shape=(32, 32, 3)))
model.add(Activation('relu'))
model.add(Conv2D(num_filters, (3,3), padding='same'))
model.add(Activation('relu'))
model.add(MaxPooling2D(pool_size=(2,2)))
model.add(Dropout(0.4))

model.add(Conv2D(2*num_filters, (3,3), padding='same'))
model.add(Activation('relu'))
model.add(Conv2D(2*num_filters, (3,3), padding='same'))
model.add(Activation('relu'))
model.add(MaxPooling2D(pool_size=(2,2)))
model.add(Dropout(0.4))

model.add(Flatten())
model.add(Dense(10, activation='softmax'))

# Summarize the model
model.summary()
plot_model(model, to_file='model_plot.png', show_shapes=True, show_layer_names=True)

Model: "sequential_2"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
conv2d_8 (Conv2D)            (None, 32, 32, 32)        896       
_________________________________________________________________
activation_8 (Activation)    (None, 32, 32, 32)        0         
_________________________________________________________________
conv2d_9 (Conv2D)            (None, 32, 32, 32)        9248      
_________________________________________________________________
activation_9 (Activation)    (None, 32, 32, 32)        0         
_________________________________________________________________
max_pooling2d_4 (MaxPooling2 (None, 16, 16, 32)        0         
_________________________________________________________________
dropout_4 (Dropout)          (None, 16, 16, 32)        0         
_________________________________________________________________
conv2d_10 (Conv2D)           (None, 16, 16, 64)       

# Validation Data

In [36]:
_X_val = []
_y_val = []
for i in range(10):
  _X_val.append(pickle.load(open(ROOT + '/cifar/labeled/X_test_label' + str(i), mode='rb')))
  _y_val.append(pickle.load(open(ROOT + '/cifar/labeled/y_test_label' + str(i), mode='rb')))

X_val = np.vstack(_X_val)
y_val = np.vstack(_y_val)

print(X_val.shape, y_val.shape)

(10000, 32, 32, 3) (10000, 10)


# Metrics

In [0]:
def get_class_label(one_hot):
  max_class_label = 0
  for class_label in range(1, len(one_hot)):
    max_class_label = max(
      (one_hot[max_class_label], max_class_label), (one_hot[class_label], class_label),
      key=lambda a: a[0]
    )[1]
  return max_class_label


def get_confusion_matrix(model, X_val, y_val):
  confusion = {class_num: np.zeros((10, 10)) for class_num in range(10)}
  for class_num in range(10):
    # get validation samples and their expected results
    class_start_row = class_num * 1000
    class_end_row = (class_num + 1) * 1000
    X_val_class = X_val[class_start_row:class_end_row, :]
    y_val_class = y_val[class_start_row:class_end_row, :]
    assert X_val_class.shape == (1000, 32, 32, 3)
    assert y_val_class.shape == (1000, 10)

    # get predicted results of the validation samples from the CNN
    batch_size = 100
    steps = 1000 // batch_size
    y_pred_class = model.predict(X_val_class, batch_size=batch_size, verbose=1, steps=steps)
    assert y_pred_class.shape == (1000, 10)

    # generate the confusion matrix of the expected and predicted results
    # of the validation samples for the current class
    for sample in range(1000):
      exp_class = get_class_label(y_val_class[sample])
      pred_class = get_class_label(y_pred_class[sample])
      assert exp_class >= 0 and exp_class < 10
      assert pred_class >= 0 and pred_class < 10
      confusion[class_num][pred_class, exp_class] += 1
    

  # concatenate the confusion matrices of each class into a single matrix
  confusion_matrix = np.zeros((10, 10))
  for class_num in confusion.keys():
    for row in range(confusion[class_num].shape[0]):
      for col in range(confusion[class_num].shape[1]):
        confusion_matrix[row, col] += confusion[class_num][row, col]
  return confusion_matrix

def get_metrics(confusion):
  true_positive = np.zeros(10)
  for i in range(10):
    true_positive[i] = confusion[i][i]
  s = np.sum(confusion, axis=0)
  false_positive = np.zeros(10)
  for i in range(10):
    false_positive[i] = s[i] - true_positive[i]
  s = np.sum(confusion, axis=1)
  false_negative = np.zeros(10)
  for i in range(10):
    false_negative[i] = s[i] - true_positive[i]
  s = np.sum(np.sum(confusion, axis=1))
  true_negative = np.zeros(10)
  for i in range(10):
    true_negative[i] = s - true_positive[i] - false_positive[i] - false_negative[i]
  accuracy = (true_positive + true_negative)/(true_positive + true_negative + false_positive + false_negative)
  recall = (true_positive)/(true_positive + false_negative)
  precision = (true_positive)/(true_positive + false_positive)
  f1 = (2 * precision * recall)/(precision + recall)
  return accuracy, recall, precision, f1

# Baseline

In [38]:
X = np.zeros((50000, 32, 32, 3)).astype(float)
y = np.zeros((50000, 10)).astype(float)
k = 0
for i in range(10):
  _X = pickle.load(open(ROOT + '/cifar/labeled/X_train_label' + str(i), mode='rb'))
  _y = pickle.load(open(ROOT + '/cifar/labeled/y_train_label' + str(i), mode='rb'))
  for j in range(5000):
    X[k] = _X[j]
    y[k] = _y[j]
    k += 1

assert(k == 50000)

# Compile the model
model.compile(optimizer='adam', loss='categorical_crossentropy', metrics=['accuracy'])

# Train the model
start = time.time()
fit_history = model.fit(X, y,
                       batch_size=128, epochs=1,
                       validation_data = (X_val, y_val),
                       shuffle=True,
                       verbose=1)
end = time.time()

# Training time
print("Model took %0.2f seconds to train"%(end - start))

# Save metrics
pctg_unlabeled = 0
confusion = get_confusion_matrix(model, X_val, y_val)
pickle.dump(confusion, open(f"{ROOT}/cifar/metrics/{pctg_unlabeled}%_unlabeled/baseline/confusion_matrix", 'wb'))
accuracy, recall, precision, f1 = get_metrics(confusion)
pickle.dump(accuracy, open(f"{ROOT}/cifar/metrics/{pctg_unlabeled}%_unlabeled/baseline/accuracy_score", 'wb'))
pickle.dump(recall, open(f"{ROOT}/cifar/metrics/{pctg_unlabeled}%_unlabeled/baseline/recall_score", 'wb'))
pickle.dump(precision, open(f"{ROOT}/cifar/metrics/{pctg_unlabeled}%_unlabeled/baseline/precision_score", 'wb'))
pickle.dump(f1, open(f"{ROOT}/cifar/metrics/{pctg_unlabeled}%_unlabeled/baseline/f1_score", 'wb'))

Train on 50000 samples, validate on 10000 samples
50000/50000 [==============================] - 6s 115us/sample - loss: 1.5906 - accuracy: 0.4233 - val_loss: 1.2841 - val_accuracy: 0.5424
Model took 5.80 seconds to train
1000/1 [==================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================

# Entropy

In [39]:
delta = 5000
for m in range(1,10):
  labeled = int(delta*m/10)
  unlabeled = 5000 - labeled

  X = np.zeros((50000, 32, 32, 3)).astype(float)
  y = np.full((50000, 10), -1).astype(float)
  k = 0
  for i in range(10):
    _X = pickle.load(open(ROOT + '/cifar/labeled/X_train_label' + str(i), mode='rb'))
    _y = pickle.load(open(ROOT + '/cifar/labeled/y_train_label' + str(i), mode='rb'))
    indices = random.sample(range(0, 5000), 5000)
    for j in range(labeled):
      X[k] = _X[indices[j]]
      y[k] = _y[indices[j]]
      k += 1
    for j in range(labeled, 5000):
      X[k] = _X[indices[j]]
      k += 1
  
  assert(k == 50000)

  # Compile the model
  model.compile(optimizer='adam', loss=custom_loss, metrics=['accuracy'])

  # Train the model
  start = time.time()
  fit_history = model.fit(X, y,
                        batch_size=128, epochs=1,
                        validation_data = (X_val, y_val),
                        shuffle=True,
                        verbose=1)
  end = time.time()

  # Training time
  print("Model took %0.2f seconds to train"%(end - start))

  # Save metrics
  pctg_unlabeled = int(unlabeled / 50000 * 100.0)
  confusion = get_confusion_matrix(model, X_val, y_val)
  pickle.dump(confusion, open(f"{ROOT}/cifar/metrics/{pctg_unlabeled}%_unlabeled/entropy/confusion_matrix", 'wb'))
  accuracy, recall, precision, f1 = get_metrics(confusion)
  pickle.dump(accuracy, open(f"{ROOT}/cifar/metrics/{pctg_unlabeled}%_unlabeled/entropy/accuracy_score", 'wb'))
  pickle.dump(recall, open(f"{ROOT}/cifar/metrics/{pctg_unlabeled}%_unlabeled/entropy/recall_score", 'wb'))
  pickle.dump(precision, open(f"{ROOT}/cifar/metrics/{pctg_unlabeled}%_unlabeled/entropy/precision_score", 'wb'))
  pickle.dump(f1, open(f"{ROOT}/cifar/metrics/{pctg_unlabeled}%_unlabeled/entropy/f1_score", 'wb'))

Train on 50000 samples, validate on 10000 samples
50000/50000 [==============================] - 7s 141us/sample - loss: 1.5572 - accuracy: 0.1428 - val_loss: 1.2915 - val_accuracy: 0.5451
Model took 7.08 seconds to train
1000/1 [==================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================

# MixUp

In [40]:
delta = 5000
for m in range(1,10):
  labeled = int(delta*m/10)
  unlabeled = 50000 - labeled*10

  X = np.zeros((50000, 32, 32, 3))
  y = np.zeros((50000, 10))
  k = 0
  for i in range(10):
    _X = pickle.load(open(ROOT + '/cifar/labeled/X_train_label' + str(i), mode='rb'))
    _y = pickle.load(open(ROOT + '/cifar/labeled/y_train_label' + str(i), mode='rb'))
    indices = random.sample(range(0, 5000), labeled)
    for j in indices:
      X[k] = _X[j]
      y[k] = _y[j]
      k += 1

  _X = pickle.load(open(ROOT + '/cifar/labeled/X_train_MixUp', mode='rb'))
  _y = pickle.load(open(ROOT + '/cifar/labeled/y_train_MixUp', mode='rb'))
  indices = random.sample(range(0, 50000), unlabeled)
  for j in indices:
    X[k] = _X[j]
    y[k] = _y[j]
    k += 1

  assert(k == 50000)

  # Compile the model
  model.compile(optimizer='adam', loss=custom_loss, metrics=['accuracy'])

  # Train the model
  start = time.time()
  fit_history = model.fit(X, y,
                        batch_size=128, epochs=1,
                        validation_data = (X_val, y_val),
                        shuffle=True,
                        verbose=1)
  end = time.time()

  # Training time
  print("Model took %0.2f seconds to train"%(end - start))

  # Save metrics
  pctg_unlabeled = int(unlabeled / 50000 * 100.0)
  confusion = get_confusion_matrix(model, X_val, y_val)
  pickle.dump(confusion, open(f"{ROOT}/cifar/metrics/{pctg_unlabeled}%_unlabeled/mixup/confusion_matrix", 'wb'))
  accuracy, recall, precision, f1 = get_metrics(confusion)
  pickle.dump(accuracy, open(f"{ROOT}/cifar/metrics/{pctg_unlabeled}%_unlabeled/mixup/accuracy_score", 'wb'))
  pickle.dump(recall, open(f"{ROOT}/cifar/metrics/{pctg_unlabeled}%_unlabeled/mixup/recall_score", 'wb'))
  pickle.dump(precision, open(f"{ROOT}/cifar/metrics/{pctg_unlabeled}%_unlabeled/mixup/precision_score", 'wb'))
  pickle.dump(f1, open(f"{ROOT}/cifar/metrics/{pctg_unlabeled}%_unlabeled/mixup/f1_score", 'wb'))


Train on 50000 samples, validate on 10000 samples
50000/50000 [==============================] - 6s 129us/sample - loss: 0.8875 - accuracy: 0.5819 - val_loss: 0.9100 - val_accuracy: 0.6994
Model took 6.51 seconds to train
1000/1 [==================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================

# CutMix

In [41]:
delta = 5000
for m in range(1,10):
  labeled = int(delta*m/10)
  unlabeled = 50000 - labeled*10

  X = np.zeros((50000, 32, 32, 3))
  y = np.zeros((50000, 10))
  k = 0
  for i in range(10):
    _X = pickle.load(open(ROOT + '/cifar/labeled/X_train_label' + str(i), mode='rb'))
    _y = pickle.load(open(ROOT + '/cifar/labeled/y_train_label' + str(i), mode='rb'))
    indices = random.sample(range(0, 5000), labeled)
    for j in indices:
      X[k] = _X[j]
      y[k] = _y[j]
      k += 1

  _X = pickle.load(open(ROOT + '/cifar/labeled/X_train_CutMix', mode='rb'))
  _y = pickle.load(open(ROOT + '/cifar/labeled/y_train_CutMix', mode='rb'))
  indices = random.sample(range(0, 50000), unlabeled)
  for j in indices:
    X[k] = _X[j]
    y[k] = _y[j]
    k += 1

  assert(k == 50000)

  # Compile the model
  model.compile(optimizer='adam', loss=custom_loss, metrics=['accuracy'])

  # Train the model
  start = time.time()
  fit_history = model.fit(X, y,
                        batch_size=128, epochs=1,
                        validation_data = (X_val, y_val),
                        shuffle=True,
                        verbose=1)
  end = time.time()

  # Training time
  print("Model took %0.2f seconds to train"%(end - start))

  # Save metrics
  pctg_unlabeled = int(unlabeled / 50000 * 100.0)
  confusion = get_confusion_matrix(model, X_val, y_val)
  pickle.dump(confusion, open(f"{ROOT}/cifar/metrics/{pctg_unlabeled}%_unlabeled/cutmix/confusion_matrix", 'wb'))
  accuracy, recall, precision, f1 = get_metrics(confusion)
  pickle.dump(accuracy, open(f"{ROOT}/cifar/metrics/{pctg_unlabeled}%_unlabeled/cutmix/accuracy_score", 'wb'))
  pickle.dump(recall, open(f"{ROOT}/cifar/metrics/{pctg_unlabeled}%_unlabeled/cutmix/recall_score", 'wb'))
  pickle.dump(precision, open(f"{ROOT}/cifar/metrics/{pctg_unlabeled}%_unlabeled/cutmix/precision_score", 'wb'))
  pickle.dump(f1, open(f"{ROOT}/cifar/metrics/{pctg_unlabeled}%_unlabeled/cutmix/f1_score", 'wb'))


Train on 50000 samples, validate on 10000 samples
50000/50000 [==============================] - 7s 132us/sample - loss: 0.7348 - accuracy: 0.4912 - val_loss: 0.8126 - val_accuracy: 0.7272
Model took 6.66 seconds to train
1000/1 [==================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================